# Data 201

Data Wrangling, S2 2021

## Assignement 2

### 20% of final grade

## Due date: 2pm Tuesday 12 October 2021

The assignment must be submitted on the DATA 201 and 422 Learn page and should be **your own pair** (or group of three if we are odd) **work**. Avoid plagiarism: if you are not sure what may constitute code plagiarism, read this http://web.science.mq.edu.au/~mtaylor/ponline/index.php?id=source-code-plagiarism. Remember, when in doubt **declare your sources**.  
As a general rule, late submission are **highly** unsuggested. The pace of the course is very quick, and you don't want to be working on this too long, as you would have less time for other assignments. I suggest you to submit what you have ready by the time the assignment is due, even if it is not everything we required. For any particular problem, please contact [Thomas Li](thomas.li@canterbury.ac.nz) or [Giulio Dalla Riva](giulio.dallariva@canterbury.ac.nz) or TAs.


## Instruction

### Total: 20 marks.

For this assignment you will work with data from the web. Your goal is to scrape it or request it, wrangle it, produce some plotting, in order to demonstrate that you are able to use the functions, plotting, and markdown format we have been learning.  
You shall hand in your work as a jupyter R notebook comprehending the code, the plots and, **very important**, enough comments and explanations for us to understand what you did, how you did it, and why you did it. Remember: better comments, means better marks.  
You can either modify this notebook or write a new one from scratch.

Do use the tidyverse syntax that's introduced in class and labs. If in doubt, refresh the lab material 1 to 7.

### Task (a): scrape it (5 marks)

Identify a website page showing information you find interesting. The information should be presented across more than one page. Select one of this pages (the rest is for later) and using `rvest` (and the suit of `tidyverse` libraries we used so far, plus any other one you may need) get the html into R.

tidyverse: collection of R packages
rvest: read webpage and expore content.

In [1]:
library(tidyverse)
library(rvest)



── Attaching packages ─────────────────────────────────────── tidyverse 1.3.1 ──

✔ ggplot2 3.3.5     ✔ purrr   0.3.4
✔ tibble  3.1.3     ✔ dplyr   1.0.7
✔ tidyr   1.1.3     ✔ stringr 1.4.0
✔ readr   1.4.0     ✔ forcats 0.5.1

── Conflicts ────────────────────────────────────────── tidyverse_conflicts() ──
✖ dplyr::filter() masks stats::filter()
✖ dplyr::lag()    masks stats::lag()


Attaching package: ‘rvest’


The following object is masked from ‘package:readr’:

    guess_encoding




In [2]:

#use readed course url to get all details we want
get_text <- function(url_readed,selector){
        text_need <- url_readed %>%
                        html_elements(selector) %>%
                        html_text()
        return(text_need)
    }

get_detail <- function(web_url){
    url_readed <- web_url %>% read_html() 
    node_selector <- "#ctl00_ContentPlaceHolder1_CourseCodeLabel"
    course_code <- get_text(url_readed, node_selector)
    if (identical(course_code, character(0))){
        course_code = 'NULL'
    }

    node_selector <- "#ctl00_ContentPlaceHolder1_CourseOccurrenceTitleLabel"
    course_name <- get_text(url_readed, node_selector)
    if (identical(course_name, character(0))){
        course_name = 'NULL'
    }

    node_selector <- "#ctl00_ContentPlaceHolder1_DomesticFeeLabel"
    Domestic_fee <- get_text(url_readed, node_selector)
    if (identical(Domestic_fee, character(0))){
        Domestic_fee = 'NULL'
    }

    node_selector <- "#ctl00_ContentPlaceHolder1_InternationalFeeLabel"
    International_fee <- get_text(url_readed, node_selector)
    if (identical(International_fee, character(0))){
        International_fee = 'NULL'
    }

    node_selector <- "#ctl00_ContentPlaceHolder1_StartDateLabel"
    Start_date <- get_text(url_readed, node_selector)
    if (identical(Start_date, character(0))){
        Start_date = 'NULL'
    }

    node_selector <- "#ctl00_ContentPlaceHolder1_EndDateLabel"
    End_date <- get_text(url_readed, node_selector)
    if (identical(End_date, character(0))){
        End_date = 'NULL'
    }

    node_selector <- "#ctl00_ContentPlaceHolder1_PointsAndEftsLabel"
    Points <- get_text(url_readed, node_selector)
    if (identical(Points, character(0))){
        Points = 'NULL'
    }
    lecturers <- get_lecturers(url_readed, course_code)
    return(list(course_code, course_name, Domestic_fee, International_fee, Start_date, End_date, Points, lecturers))
}


In [3]:
base_lecturer_url <- 'https://www.canterbury.ac.nz/courseinfo/'
get_lecturers <- function(url_readed, course_code) {
    lecturer_links <- url_readed %>% html_element('#ctl00_ContentPlaceHolder1_ContributorsDiv') %>% html_elements('a')
    names = c()
    links = c()
    emails = c()
    titles = c()
    rooms = c()
    phones = c()
    for (lecturer in lecturer_links){
        name <- lecturer %>% html_text()
        link <- lecturer %>% html_attr('href')

        if (is.na(link)){
            next
        }
        if (endsWith(link, 'contact-us')){
            link <- NA;
        }
        if (startsWith(link, 'ShowPeopleDetails')){
            link <- paste(base_lecturer_url, link, sep='')
        }
        if (name == 'Language, Social and Political Sciences'){
            name <- NA
        }
        if(!is.na(name)){
            names <- c(names, name)
            links <- c(links, link)
            lecturer_data = get_lecturer(link)
            emails <- c(emails, lecturer_data[1])
            titles <- c(titles, lecturer_data[2])
            rooms <- c(rooms, lecturer_data[3])
            phones <- c(phones, lecturer_data[4])   
        }
    }
    return(tibble(course_code=course_code, names=names, links=links, emails=emails, titles=titles, rooms=rooms, phones=phones))
}


In [4]:
get_lecturer <- function(url){
    header <- 'div.staff-profile-header'
    tryCatch( { 
    #open connection to url 
        page <- url %>% read_html()
        header_object <- page %>% html_node(header)
    }, error = function(e){
        return(c(NA, NA, NA, NA))
    }
    )
    if(!exists("header_object")){
        return(c(NA, NA, NA, NA))
    }
    if (is.na(header_object) | is.null(header_object)) {
        data <-  c(NA, NA, NA, NA);
    }else{
        email <- page %>% html_node('.staff-profile-email') %>% html_text()
        title <- header_object %>% html_node('h2') %>% html_node('span') %>% html_text()
        room <- header_object %>% html_node('.col-sm-8 div:nth-child(6)') %>% html_text()
        phone <- header_object %>% html_node('.col-sm-8 div:nth-child(7)') %>% html_text()
        data <- c(email, title, room, phone)
    }
    return(data)
}

In [5]:
url_adreess_French <- "https://www.canterbury.ac.nz/courseinfo/GetCourses.aspx?subjectnames=French&viewby=subject&year2021"                    
url_adreess_French <- 'https://www.canterbury.ac.nz/courseinfo/GetCourses.aspx?subjectnames=Science%20Education&viewby=subject&year2021'              
one_subject_all_courses_detetal <- function(subject_url){
    new_table <- data.frame("course_code"=0, "course_name"=0,
                            "domestic_fee"=0, "international_fee"=0, 
                            "start_date"=0, "end_date"=0, 
                            "points"=0, 'link'=0)
    
    tryCatch( 
        { 
        #open connection to url 
            read_url_subjects <- subject_url %>% read_html()
            all_links <- read_url_subjects %>% html_element("#GetCourses") %>% html_elements('a')
        }, error = function(e){
            return(c(new_table, c(NA, NA, NA, NA)))
        }
    )
    if (!exists('all_links')){
        return(c(new_table, c(NA, NA, NA, NA)))
    }
    if (length(all_links) == 0 ){
        return(c(new_table, c(NA, NA, NA, NA)))
    }else{
        table_a_tage <- bind_rows(lapply(html_attrs(all_links),
                                  function(x) data.frame(as.list(x), stringsAsFactors=FALSE)))
    }
    prefix <- "https://www.canterbury.ac.nz/courseinfo/"
    table_a_tage_without_na <- table_a_tage[3] %>% filter(href!="NA") %>% mutate(href = str_c(prefix, href))   
    max_row <- nrow(table_a_tage_without_na)
    lecturer_list = c()
    for (i in 1:max_row){
         a <- table_a_tage_without_na[i,]
         b <- a %>% get_detail()
         lecturer_list <- c(lecturer_list, b[8])
         new_table[nrow(new_table) + 1,] = c(b[1], b[2], b[3], b[4], b[5], b[6], b[7], a)

    }
    delet_first_row <- new_table[-1,]
    lecturer_list <- lecturer_list %>% bind_rows() %>% as.data.frame()
    return(list(delet_first_row, lecturer_list)) 
}

#one_subject_all_courses_detetal(url_adreess_French)                

In [37]:
#https://www.canterbury.ac.nz/courseinfo/GetCourses.aspx?subjectnames=French&viewby=subject&year2021
url_adreess_subjects <- "https://www.canterbury.ac.nz/courseinfo/subjects.aspx"

get_all_courses <- function(subjects_url){
    subjects = c()
    lecturers = c()
    url_subjects_a <- url_adreess_subjects %>% read_html() %>% html_elements('.row') %>% html_elements('.col-md-6') %>% html_elements('a')
    table_a_tage <- bind_rows(lapply(html_attrs(url_subjects_a), function(x) data.frame(as.list(x), stringsAsFactors=FALSE)))
    max_row <- nrow(table_a_tage)
    
    prefix_subject <- "https://www.canterbury.ac.nz/courseinfo/"
    for(i in 1:max_row){
        one_subject_url <- table_a_tage[i,2] %>% str_c(prefix_subject,.) %>% str_replace_all(" ", "%20")
       # if (one_subject_url != 'https://www.canterbury.ac.nz/courseinfo/GetCourses.aspx?subjectnames=Science%20Education&viewby=subject&year2021'){
        course_info <- one_subject_all_courses_detetal(one_subject_url)
        if (lengths(course_info[1]) == 1){
            next
        }
        tryCatch({ 
            subjects <- c(subjects, course_info[1])
            lecturers <- c(lecturers, course_info[2])
        }, error = function(e){})

    }
    lecturers <- lecturers %>% bind_rows()
    subjects <- subjects %>% bind_rows()
    return(list(subjects, lecturers))
                                     
}
course_data <- get_all_courses(url_adreess_subjects) 
course_data[1]
course_data[2]

[[1]]
           course_code
1     FREN121-21S1 (C)
2     FREN122-21S2 (C)
3     FREN211-21S2 (C)
4     FREN221-21S1 (C)
5     FREN222-21S2 (C)
6     FREN311-21S2 (C)
7     FREN321-21S1 (C)
8     FREN322-21S2 (C)
9     FREN401-21S1 (C)
10    FREN418-21S2 (C)
11    FREN422-21S2 (C)
12    FREN480-21S2 (C)
13     FREN650-21A (C)
14    FREN650-21S1 (C)
15    FREN650-21S2 (C)
16     FREN690-21A (C)
17     FREN790-21A (C)
18    LANC401-21S1 (C)
19    LANC403-21S1 (C)
20             FREN106
21             FREN120
22             FREN223
23             FREN226
24             FREN323
25             FREN326
26             FREN444
27    ACCT624-21S2 (C)
28    ECON323-21S2 (C)
29    ECON331-21S2 (C)
30    ECON344-21S2 (C)
31    ECON641-21S2 (C)
32    ECON643-21S1 (C)
33    FINC101-21S1 (C)
34   FINC101-21SU1 (C)
35    FINC201-21S1 (C)
36    FINC201-21S2 (C)
37    FINC203-21S1 (C)
38    FINC301-21S2 (C)
39    FINC305-21S1 (C)
40    FINC308-21S2 (C)
41    FINC311-21S1 (C)
42    FINC312-21S1 (C)
43    FINC331-21S2 (C)
44    FINC344-21S2 (C)
45    FINC390-21S1 (C)
46    FINC390-21S2 (C)
47    FINC608-21S2 (C)
48    FINC610-21S1 (C)
49    FINC610-21S2 (C)
50    FINC612-21S1 (C)
51    FINC613-21S1 (C)
52    FINC613-21S2 (C)
53    FINC614-21S1 (C)
54    FINC616-21S1 (C)
55    FINC618-21S2 (C)
56    FINC623-21S2 (C)
57    FINC629-21S1 (C)
58    FINC641-21S2 (C)
59    FINC643-21S1 (C)
60    FINC650-21S2 (C)
61    FINC679-21S1 (C)
62    FINC679-21S2 (C)
63   FINC679-21SU2 (C)
64     FINC680-21W (C)
65     FINC691-21A (C)
66     FINC694-21A (C)
67     FINC695-21A (C)
68     FINC699-21A (C)
69     FINC790-21A (C)
70    STAT317-21S2 (C)
71             ACCT625
72             ECON345
73             ECON622
74             FINC205
75             FINC302
76             FINC316
77             FINC323
78             FINC345
79             FINC370
80             FINC621
81             FINC622
82             FINC624
83             FINC625
84             FINC626
85             FINC627
86             FINC628
87             FINC649
88                NULL
89                NULL
90                NULL
91     MFIN670-21X (C)
92                NULL
93                NULL
94                NULL
95                NULL
96    FORE102-21S1 (D)
97    FORE102-21S2 (D)
98    FORE105-21S1 (D)
99    FORE105-21S2 (D)
100  FORE105-21SU2 (D)
101   FORE111-21S1 (C)
102   FORE131-21S2 (C)
103   FORE141-21S2 (C)
104   FORE151-21S1 (C)
105   FORE205-21S1 (C)
106   FORE215-21S2 (C)
107   FORE218-21S1 (C)
108   FORE219-21S2 (C)
109   FORE222-21S1 (C)
110   FORE224-21S2 (C)
111   FORE307-21S1 (C)
112   FORE316-21S2 (C)
113   FORE327-21S2 (C)
114   FORE342-21S1 (C)
115    FORE414-21W (C)
116   FORE419-21S1 (C)
117    FORE419-21W (C)
118   FORE422-21S1 (C)
119   FORE423-21S2 (C)
120   FORE426-21S1 (C)
121   FORE435-21S2 (C)
122   FORE436-21S1 (C)
123   FORE443-21S2 (C)
124   FORE447-21S2 (C)
125   FORE475-21S1 (C)
126   FORE475-21S2 (C)
127    FORE475-21W (C)
128   FORE610-21S1 (C)
129   FORE610-21S2 (C)
130   FORE616-21S2 (C)
131   FORE618-21S2 (C)
132   FORE619-21S2 (C)
133   FORE624-21S1 (C)
134   FORE641-21S2 (C)
135   FORE642-21S1 (C)
136   FORE643-21S1 (D)
137   FORE643-21S2 (D)
138   FORE675-21S1 (C)
139   FORE675-21S2 (C)
140    FORE675-21W (C)
141    FORE679-21A (C)
142   FORE679-21S1 (C)
143   FORE679-21S2 (C)
144    FORE690-21A (C)
145    FORE790-21A (C)
146            FORE672
147  FIEC601-21SU1 (C)
148  FIEC601-21SU1 (D)
149  FIEC675-21SU2 (C)
150   FINA101-21S1 (C)
151   FINA102-21S1 (C)
152   FINA103-21S2 (C)
153    FINA450-21W (C)
154    FINA451-21W (C)
155    FINA452-21W (C)
156   ENFE601-21S1 (C)
157   ENFE602-21S1 (C)
158    ENFE603-21X (C)
159    ENFE605-21X (C)
160    ENFE610-21X (C)
161   ENFE615-21S1 (C)
162   ENFE675-21S1 (C)
163   ENFE675-21S2 (C)
164    ENFE675-21W (C)
165    ENFE681-21A (C)
166  ENFE681-21SU2 (C)
167    ENFE682-21A (C)
168  ENFE682-21SU2 (C)
169    ENFE683-21A (C)
170  ENFE683-21SU2 (C)
171    ENFE690-21A (C)
172    ENFE790-21A (C)
173            

[[1]]
           course_code
1     FREN121-21S1 (C)
2     FREN121-21S1 (C)
3     FREN122-21S2 (C)
4     FREN211-21S2 (C)
5     FREN221-21S1 (C)
6     FREN221-21S1 (C)
7     FREN221-21S1 (C)
8     FREN222-21S2 (C)
9     FREN222-21S2 (C)
10    FREN311-21S2 (C)
11    FREN321-21S1 (C)
12    FREN321-21S1 (C)
13    FREN322-21S2 (C)
14    FREN322-21S2 (C)
15    FREN401-21S1 (C)
16    FREN418-21S2 (C)
17    FREN422-21S2 (C)
18    FREN480-21S2 (C)
19     FREN650-21A (C)
20    FREN650-21S1 (C)
21    FREN650-21S2 (C)
22     FREN690-21A (C)
23     FREN790-21A (C)
24    LANC401-21S1 (C)
25    LANC403-21S1 (C)
26             FREN106
27             FREN120
28             FREN223
29             FREN226
30             FREN323
31             FREN326
32             FREN444
33    ACCT624-21S2 (C)
34    ACCT624-21S2 (C)
35    ECON323-21S2 (C)
36    ECON323-21S2 (C)
37    ECON331-21S2 (C)
38    ECON344-21S2 (C)
39    ECON641-21S2 (C)
40    ECON643-21S1 (C)
41    FINC101-21S1 (C)
42   FINC101-21SU1 (C)
43    FINC201-21S1 (C)
44    FINC201-21S2 (C)
45    FINC203-21S1 (C)
46    FINC301-21S2 (C)
47    FINC305-21S1 (C)
48    FINC308-21S2 (C)
49    FINC311-21S1 (C)
50    FINC312-21S1 (C)
51    FINC331-21S2 (C)
52    FINC344-21S2 (C)
53    FINC390-21S1 (C)
54    FINC390-21S2 (C)
55    FINC608-21S2 (C)
56    FINC610-21S1 (C)
57    FINC610-21S2 (C)
58    FINC612-21S1 (C)
59    FINC613-21S1 (C)
60    FINC613-21S2 (C)
61    FINC614-21S1 (C)
62    FINC616-21S1 (C)
63    FINC618-21S2 (C)
64    FINC623-21S2 (C)
65    FINC629-21S1 (C)
66    FINC641-21S2 (C)
67    FINC643-21S1 (C)
68    FINC650-21S2 (C)
69    FINC679-21S1 (C)
70    FINC679-21S2 (C)
71   FINC679-21SU2 (C)
72     FINC680-21W (C)
73     FINC691-21A (C)
74     FINC694-21A (C)
75     FINC695-21A (C)
76     FINC699-21A (C)
77     FINC790-21A (C)
78    STAT317-21S2 (C)
79    STAT317-21S2 (C)
80             ACCT625
81             ECON345
82             ECON622
83             FINC205
84             FINC302
85             FINC316
86             FINC323
87             FINC345
88             FINC370
89             FINC621
90             FINC622
91             FINC624
92             FINC625
93             FINC626
94             FINC627
95             FINC628
96             FINC649
97                NULL
98                NULL
99                NULL
100    MFIN670-21X (C)
101               NULL
102               NULL
103               NULL
104               NULL
105   FORE102-21S1 (D)
106   FORE102-21S2 (D)
107   FORE105-21S1 (D)
108   FORE105-21S2 (D)
109  FORE105-21SU2 (D)
110   FORE111-21S1 (C)
111   FORE111-21S1 (C)
112   FORE131-21S2 (C)
113   FORE141-21S2 (C)
114   FORE151-21S1 (C)
115   FORE205-21S1 (C)
116   FORE215-21S2 (C)
117   FORE218-21S1 (C)
118   FORE218-21S1 (C)
119   FORE219-21S2 (C)
120   FORE222-21S1 (C)
121   FORE224-21S2 (C)
122   FORE307-21S1 (C)
123   FORE316-21S2 (C)
124   FORE327-21S2 (C)
125   FORE342-21S1 (C)
126    FORE414-21W (C)
127   FORE419-21S1 (C)
128    FORE419-21W (C)
129   FORE422-21S1 (C)
130   FORE423-21S2 (C)
131   FORE423-21S2 (C)
132   FORE426-21S1 (C)
133   FORE435-21S2 (C)
134   FORE436-21S1 (C)
135   FORE443-21S2 (C)
136   FORE447-21S2 (C)
137   FORE475-21S1 (C)
138   FORE475-21S2 (C)
139    FORE475-21W (C)
140   FORE610-21S1 (C)
141   FORE610-21S2 (C)
142   FORE616-21S2 (C)
143   FORE618-21S2 (C)
144   FORE619-21S2 (C)
145   FORE624-21S1 (C)
146   FORE641-21S2 (C)
147   FORE642-21S1 (C)
148   FORE643-21S1 (D)
149   FORE643-21S2 (D)
150   FORE675-21S1 (C)
151   FORE675-21S2 (C)
152    FORE675-21W (C)
153    FORE679-21A (C)
154   FORE679-21S1 (C)
155   FORE679-21S2 (C)
156    FORE690-21A (C)
157    FORE790-21A (C)
158            FORE672
159  FIEC601-21SU1 (C)
160  FIEC601-21SU1 (D)
161  FIEC675-21SU2 (C)
162   FINA101-21S1 (C)
163   FINA101-21S1 (C)
164   FINA102-21S1 (C)
165   FINA102-21S1 (C)
166   FINA103-21S2 (C)
167   FINA103-21S2 (C)
168    FINA450-21W (C)
169    FINA450-21W (C)
170    FINA451-21W (C)
171    FINA451-21W (C)
172    FINA452-21W (C)
173    FINA452-

In [40]:
write.csv(as.data.frame(course_data[1]), 'lecturers.csv')
write.csv(as.data.frame(course_data[2]), 'lecturers.csv')

[1] "list"

### Task (b): wrangle it (5 marks)


Working on the page from task (a), transform the data you collected into relational data model (that is, one or more data frames). WARNING: you will need to think and motivate how you are doing this in terms of the **data model** you are trying to build; just throwing everything in a table is not enough.

In [ ]:
# your answer here

### Task (c): automate it (5 marks)

Now it's the time to scrape everything else in the website. Turn your code for tasks (a) and (b) into a function and using `purrr` (and its `map_` functions, possibly in combination with `possibly`) apply that function to all the pages you are interested in (as we have done in lab 6); the output of the task should be a relation dataset (i.e., one or more dataframes, and if more than one, explicit their relationships).

In [ ]:
# your answer here

### Task (d): plot it (2 marks)

Use graphics (via `ggplot`) to represent the data you collected in a meaningful way.

In [ ]:
# your answer here

### Task (e): APIs (2 marks)

Identify a web service offering data through an API. Access the API using `httr` and collect the information you care about. Convert the data into a dataframe (or more than one). Represent it graphically in a meaningful way.

In [ ]:
# your answer here

### Comment, explain and present the work in a clear way (1 marks)